In [10]:
import pandas as pd
import numpy as np

import sklearn
sklearn.set_config(transform_output="pandas")
import warnings
warnings.filterwarnings('ignore')

# Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline, make_pipeline
from sklearn.base import BaseEstimator, TransformerMixin

# Preprocessing
from sklearn.experimental import enable_iterative_imputer

from sklearn.impute import SimpleImputer, IterativeImputer
from sklearn.compose import make_column_selector
from sklearn.decomposition import PCA
from sklearn.model_selection import GridSearchCV, KFold
from sklearn.preprocessing import StandardScaler

# for model learning
from sklearn.model_selection import train_test_split, RandomizedSearchCV, cross_val_score

from sklearn.ensemble import RandomForestRegressor

from sklearn.ensemble import VotingRegressor, StackingRegressor

from catboost import CatBoostRegressor
from category_encoders import CatBoostEncoder

# Metrics
from sklearn.metrics import root_mean_squared_error


# tunning hyperparamters model
import optuna
import shap

In [2]:
import scipy.stats as stats

path = 'data/train.csv'
train = pd.read_csv(path)
z = np.abs(stats.zscore(train.iloc[:,-1]))
f = (abs(z) >= 2.8)

# train = train.loc[~f]

X, y = train.drop('SalePrice', axis=1), train['SalePrice']

In [3]:
num_features = train.select_dtypes(exclude='object')
cat_features = train.select_dtypes(include='object')

### Custom

In [11]:
class MasVnrType_modify(BaseEstimator, TransformerMixin): 
    
    def fit(self, X, y=None):
        return self
        
    def transform(self, X, y=None):
        X_copy = X.copy()

        ff = ((X_copy['MasVnrArea'] == 0)  & (X_copy['MasVnrType'] != 'NO'))
        X_copy.loc[ff,'MasVnrArea'] = X_copy['MasVnrArea'].loc[X_copy['MasVnrType'] == 'Stone'].median()
        
        f = ((X_copy['MasVnrArea'] != 0)  & (X_copy['MasVnrType'] == 'NO'))
        X_copy.loc[f,'MasVnrType'] = 'BrkFace'
        
        return X_copy

bath = ['BsmtFullBath','BsmtHalfBath','FullBath','HalfBath']

class Bath_maker(BaseEstimator, TransformerMixin): 
    
    def fit(self, X, y=None):
        return self
        
    def transform(self, X, y=None):
        X_copy = X.copy()
        X_copy['bath'] = (X_copy['BsmtFullBath']+X_copy['BsmtHalfBath']+X_copy['FullBath']+X_copy['HalfBath'])
        return X_copy

to_str = ['MSSubClass','YearBuilt','YearRemodAdd','MoSold','YrSold','GarageQual','GarageCond','GarageYrBlt']

class category_maker(BaseEstimator, TransformerMixin): 
    
    def fit(self, X, y=None):
        return self
        
    def transform(self, X, y=None):
        X_copy = X.copy()
        # print(str(X_copy))
        return X_copy.astype(str)



cools_to_fill = ['Alley', 'PoolQC','Fence','BsmtQual','BsmtCond','BsmtExposure','BsmtFinType1','BsmtFinType2', 'FireplaceQu','GarageType', 'GarageFinish','GarageQual','GarageCond','MasVnrType']
prepro1 = ColumnTransformer(
     transformers = [
        ('bath_maker',Bath_maker(), bath),
        ('to_str',category_maker(),to_str),
     ],
     verbose_feature_names_out = False,
     remainder = 'passthrough')

prepro2 = ColumnTransformer(
     transformers = [
        ('fillna' , SimpleImputer(strategy='constant', fill_value='NA') , cools_to_fill),
        ('mod_electrical', SimpleImputer(strategy='most_frequent'), ['Electrical']),
        ('MasVn_zero', SimpleImputer(strategy='constant', fill_value = 0 ), ['MasVnrArea']),
     ],
     verbose_feature_names_out = False,
     remainder = 'passthrough')

MasVnrType = ColumnTransformer(
    transformers = [
        ('MasVnrType_modify', MasVnrType_modify(), ['MasVnrArea','MasVnrType']),
    ],
    verbose_feature_names_out = False,
    remainder = 'passthrough' 
)

drop = ['BsmtFullBath','BsmtHalfBath','FullBath','HalfBath','Id','LotFrontage']#'BsmtFinType1','BsmtFinType2','BsmtFinSF1','BsmtFinSF2','BsmtExposure','2ndFlrSF','MiscFeature','Fireplaces','OpenPorchSF','EnclosedPorch','3SsnPorch']
dropper = ColumnTransformer(
     transformers = [
        ('dropper','drop', drop),
     ],
     verbose_feature_names_out = False,
     remainder = 'passthrough')


scale = ['MasVnrArea', 'LotArea', 'BsmtUnfSF', 'TotalBsmtSF', '1stFlrSF', 'LowQualFinSF', 'GrLivArea', 'GarageArea', 'WoodDeckSF', 'ScreenPorch', 'PoolArea', 'MiscVal']
scaler = ColumnTransformer(
     transformers = [
        ('scaler',StandardScaler(), scale),
     ],
     verbose_feature_names_out = False,
     remainder = 'passthrough')

encoding = ['MasVnrType',
 'bath',
 'GarageCars',
 'MSSubClass',
 'YearBuilt',
 'YearRemodAdd',
 'MoSold',
 'YrSold',
 'GarageQual',
 'GarageCond',
 'BedroomAbvGr',
 'GarageYrBlt',
 'KitchenAbvGr',
 'TotRmsAbvGrd',
 'Alley',
 'PoolQC',
 'Fence',
 'BsmtQual',
 'BsmtCond',
 'FireplaceQu',
 'GarageType',
 'GarageFinish',
 'GarageQual',
 'GarageCond',
 'Electrical',
 'MSZoning',
 'Street',
 'LotShape',
 'LandContour',
 'Utilities',
 'LotConfig',
 'LandSlope',
 'Neighborhood',
 'Condition1',
 'Condition2',
 'BldgType',
 'HouseStyle',
 'RoofStyle',
 'RoofMatl',
 'Exterior1st',
 'Exterior2nd',
 'ExterQual',
 'ExterCond',
 'Foundation',
 'Heating',
 'HeatingQC',
 'CentralAir',
 'KitchenQual',
 'Functional',
 'PavedDrive',
 'SaleType',
 'SaleCondition']

encoder = ColumnTransformer(
     transformers = [
        ('encode',CatBoostEncoder(),make_column_selector())
     ],
     verbose_feature_names_out = False,
     remainder = 'passthrough')

preprocessor = Pipeline(
    [
        ('stage 1', prepro1),
        ('stage 2', prepro2),
        ('drop',dropper),
        ('Custom',MasVnrType),
        ('scaler',scaler),
        ('encoder',encoder)
    ]
)

### Pipeline

In [12]:
X, y = train.drop('SalePrice', axis=1), train['SalePrice']
path = 'data/test.csv'
test =  pd.read_csv(path)
X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.2, random_state=42)

### SHAP

In [17]:
shap.initjs()

shap_X = X

model = CatBoostRegressor(iterations=3500, learning_rate=0.04,depth=4, random_seed=42)
model.fit(shap_X, y, verbose=False, plot=False)

explainer = shap.TreeExplainer(model)
shap_values = explainer.shap_values(shap_X)

vals = np.abs(shap_values).mean(0)
feature_importance = pd.DataFrame(list(zip(shap_X.columns,vals)),columns=['col_name','power'])
feature_importance.sort_values(by=['power'],ascending=False,inplace=True)


f = feature_importance.power > feature_importance.power.mean()
few = feature_importance.loc[f]['col_name']

In [19]:
feature_importance

col_name         power
1  OverallQual  44335.641826
0      LotArea  20411.035604
2  OverallCond   4078.353889

### OPTUNE

In [112]:
ml_pipeline = Pipeline(
    [
        ('preprocessor', preprocessor),
        ('model', CatBoostRegressor())
    ]
)


def objective(trial):

    model_params = {
        'iterations': trial.suggest_int('n_estimators', 400, 400, 1),
        'depth' : trial.suggest_int('max_depth', 2, 10, 1),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.2),
        'random_state': trial.suggest_int('random_state', 42, 42, 1)
    }
    
    
    ml_pipeline.named_steps['model'].set_params(**model_params)

    cv = KFold(n_splits=6, random_state=42, shuffle=True)
    
    return cross_val_score(ml_pipeline, X, y, cv=cv).mean()

study = optuna.create_study(direction='maximize')

study.optimize(objective, n_trials=40)

best_params = study.best_params
best_value = study.best_value


print(f"Лучшие параметры: {best_params}")
print(f"Лучшее значение: {best_value}")

[I 2024-02-09 15:07:19,390] A new study created in memory with name: no-name-a9cfb600-c49a-4bf6-a22d-e8b3e5ce6665


0:	learn: 71146.6313425	total: 15.5ms	remaining: 6.2s
1:	learn: 65162.7306563	total: 29ms	remaining: 5.78s
2:	learn: 60029.4014705	total: 41.6ms	remaining: 5.51s
3:	learn: 55212.1589942	total: 54.4ms	remaining: 5.39s
4:	learn: 51364.9213813	total: 66.7ms	remaining: 5.27s
5:	learn: 48130.0518377	total: 79ms	remaining: 5.19s
6:	learn: 44955.5815390	total: 91.6ms	remaining: 5.14s
7:	learn: 42119.2080698	total: 104ms	remaining: 5.12s
8:	learn: 39683.2381535	total: 118ms	remaining: 5.12s
9:	learn: 37588.8200330	total: 131ms	remaining: 5.12s
10:	learn: 35804.7472857	total: 144ms	remaining: 5.1s
11:	learn: 34054.8051311	total: 157ms	remaining: 5.09s
12:	learn: 32454.9603213	total: 170ms	remaining: 5.06s
13:	learn: 31068.7964624	total: 183ms	remaining: 5.05s
14:	learn: 29731.3995746	total: 198ms	remaining: 5.08s
15:	learn: 28587.4678370	total: 211ms	remaining: 5.06s
16:	learn: 27670.7974957	total: 223ms	remaining: 5.03s
17:	learn: 26669.6993498	total: 236ms	remaining: 5.01s
18:	learn: 25796.48

[I 2024-02-09 15:07:55,734] Trial 0 finished with value: 0.8547240500624985 and parameters: {'n_estimators': 400, 'max_depth': 9, 'learning_rate': 0.14570455316834177, 'random_state': 42}. Best is trial 0 with value: 0.8547240500624985.


396:	learn: 462.9373348	total: 5.68s	remaining: 42.9ms
397:	learn: 458.6856488	total: 5.7s	remaining: 28.6ms
398:	learn: 453.4575698	total: 5.71s	remaining: 14.3ms
399:	learn: 447.8598240	total: 5.72s	remaining: 0us
0:	learn: 71587.6333329	total: 25.5ms	remaining: 10.2s
1:	learn: 66462.3270538	total: 49.6ms	remaining: 9.88s
2:	learn: 62110.9767517	total: 73.7ms	remaining: 9.75s
3:	learn: 57762.0641061	total: 99.1ms	remaining: 9.81s
4:	learn: 53821.5502301	total: 126ms	remaining: 9.92s
5:	learn: 50867.1874042	total: 151ms	remaining: 9.92s
6:	learn: 47455.4198003	total: 176ms	remaining: 9.87s
7:	learn: 44801.2703955	total: 201ms	remaining: 9.83s
8:	learn: 42288.4142058	total: 226ms	remaining: 9.81s
9:	learn: 40195.7502595	total: 252ms	remaining: 9.82s
10:	learn: 38148.1855860	total: 276ms	remaining: 9.77s
11:	learn: 36142.7162249	total: 300ms	remaining: 9.71s
12:	learn: 34411.2536484	total: 325ms	remaining: 9.66s
13:	learn: 32918.8889286	total: 350ms	remaining: 9.66s
14:	learn: 31462.204

[I 2024-02-09 15:08:56,943] Trial 1 finished with value: 0.8551119531137216 and parameters: {'n_estimators': 400, 'max_depth': 10, 'learning_rate': 0.1366025272483755, 'random_state': 42}. Best is trial 1 with value: 0.8551119531137216.


...

300:	learn: 7009.2860488	total: 192ms	remaining: 63ms
301:	learn: 6999.0330684	total: 192ms	remaining: 62.4ms
302:	learn: 6969.6471673	total: 193ms	remaining: 61.8ms
303:	learn: 6944.2998327	total: 194ms	remaining: 61.2ms
304:	learn: 6919.5987306	total: 194ms	remaining: 60.6ms
305:	learn: 6890.6880915	total: 195ms	remaining: 60ms
306:	learn: 6872.8217789	total: 196ms	remaining: 59.4ms
307:	learn: 6854.8376037	total: 197ms	remaining: 58.7ms
308:	learn: 6842.9197143	total: 197ms	remaining: 58.1ms
309:	learn: 6829.5205889	total: 198ms	remaining: 57.5ms
310:	learn: 6797.8523365	total: 199ms	remaining: 56.9ms
311:	learn: 6768.2683322	total: 199ms	remaining: 56.3ms
312:	learn: 6745.2050659	total: 200ms	remaining: 55.6ms
313:	learn: 6715.8822218	total: 201ms	remaining: 55ms
314:	learn: 6708.2928808	total: 202ms	remaining: 54.5ms
315:	learn: 6702.0484113	total: 203ms	remaining: 53.8ms
316:	learn: 6679.1670019	total: 203ms	remaining: 53.2ms
317:	learn: 6652.7274882	total: 204ms	remaining: 52.6m

[I 2024-02-09 15:14:00,213] Trial 38 finished with value: 0.8832487625777848 and parameters: {'n_estimators': 400, 'max_depth': 5, 'learning_rate': 0.14687381993025478, 'random_state': 42}. Best is trial 11 with value: 0.8919462964568147.


354:	learn: 5398.1951331	total: 388ms	remaining: 49.1ms
355:	learn: 5389.3757863	total: 389ms	remaining: 48.1ms
356:	learn: 5354.9122445	total: 390ms	remaining: 47ms
357:	learn: 5346.4545422	total: 391ms	remaining: 45.9ms
358:	learn: 5333.8573026	total: 393ms	remaining: 44.8ms
359:	learn: 5303.2973141	total: 394ms	remaining: 43.7ms
360:	learn: 5278.9202971	total: 395ms	remaining: 42.6ms
361:	learn: 5258.8866191	total: 396ms	remaining: 41.5ms
362:	learn: 5253.1385777	total: 397ms	remaining: 40.4ms
363:	learn: 5225.7844261	total: 398ms	remaining: 39.3ms
364:	learn: 5213.2981154	total: 399ms	remaining: 38.2ms
365:	learn: 5194.9740733	total: 400ms	remaining: 37.1ms
366:	learn: 5177.9826298	total: 401ms	remaining: 36ms
367:	learn: 5163.8583792	total: 402ms	remaining: 34.9ms
368:	learn: 5137.6278960	total: 403ms	remaining: 33.8ms
369:	learn: 5124.0027660	total: 404ms	remaining: 32.7ms
370:	learn: 5112.0442656	total: 405ms	remaining: 31.6ms
371:	learn: 5097.2405262	total: 406ms	remaining: 30.

[I 2024-02-09 15:14:06,092] Trial 39 finished with value: 0.8886750450125834 and parameters: {'n_estimators': 400, 'max_depth': 6, 'learning_rate': 0.05034074256759598, 'random_state': 42}. Best is trial 11 with value: 0.8919462964568147.


324:	learn: 11538.1069283	total: 579ms	remaining: 134ms
325:	learn: 11504.4129261	total: 580ms	remaining: 132ms
326:	learn: 11485.4839226	total: 582ms	remaining: 130ms
327:	learn: 11461.4530649	total: 584ms	remaining: 128ms
328:	learn: 11440.5566738	total: 586ms	remaining: 126ms
329:	learn: 11413.9790909	total: 587ms	remaining: 125ms
330:	learn: 11386.3143870	total: 589ms	remaining: 123ms
331:	learn: 11373.5040267	total: 590ms	remaining: 121ms
332:	learn: 11348.1627287	total: 592ms	remaining: 119ms
333:	learn: 11334.2110611	total: 593ms	remaining: 117ms
334:	learn: 11293.4422782	total: 595ms	remaining: 115ms
335:	learn: 11263.3567400	total: 597ms	remaining: 114ms
336:	learn: 11230.2125564	total: 598ms	remaining: 112ms
337:	learn: 11206.7573604	total: 600ms	remaining: 110ms
338:	learn: 11186.5575473	total: 601ms	remaining: 108ms
339:	learn: 11164.9108277	total: 603ms	remaining: 106ms
340:	learn: 11138.4444394	total: 605ms	remaining: 105ms
341:	learn: 11109.0388015	total: 607ms	remaining

### CROSS VALIDATION

In [89]:
from xgboost import XGBRegressor
xgb = XGBRegressor(max_death=6, learning_rate = 0.02, n_estimators = 1000)
rfg = RandomForestRegressor(n_estimators=1000,max_depth=6,random_state=42)
cbr = CatBoostRegressor(iterations=3000, learning_rate=0.04,depth=6, random_seed=42)

# STC = StackingRegressor(
#     estimators=[
#         # ('RFR',rfg),
#         ('xgboost',xgb),
#         # ('svr',svr),
#         ('cbr',cbr)],
#     )

# STC = VotingRegressor(
#     estimators=[
#         # ('RFR',rfg),
#         ('xgboost',xgb),
#         # ('svr',svr),
#         ('cbr',cbr)],
#     )

models = {'catboost':cbr, 'XGBoost':xgb,'rfg':rfg}

cv = KFold(n_splits=5, random_state=42, shuffle=True)
d = []
for name, model in models.items():
    ml_pipeline = Pipeline(
    [
        ('preprocessor', preprocessor),
        (name, model)
    ]
)
    ml_pipeline.fit(X_train, y_train)

    train = root_mean_squared_error(y_train, ml_pipeline.predict(X_train))
    valid = root_mean_squared_error(y_valid, ml_pipeline.predict(X_valid))
    

    
    cross_validation_result = cross_val_score(
        ml_pipeline,
        X,
        y,
        cv = cv,)
    
    x = [name, train, valid, cross_validation_result.mean()]
    d.append(x)

final = pd.DataFrame(d).rename(columns={0:'Model',1:'train score',2:'valid score',3:'cross validation'}).sort_values('cross validation', ascending = False)

0:	learn: 65450.4815543	total: 1.82ms	remaining: 5.46s
1:	learn: 63895.1805061	total: 3.13ms	remaining: 4.68s
2:	learn: 62297.1375405	total: 4.29ms	remaining: 4.28s
3:	learn: 60786.7275075	total: 5.72ms	remaining: 4.29s
4:	learn: 59338.2975993	total: 6.9ms	remaining: 4.13s
5:	learn: 57906.1848610	total: 8.12ms	remaining: 4.05s
6:	learn: 56517.7362356	total: 9.36ms	remaining: 4s
7:	learn: 55215.7778752	total: 10.5ms	remaining: 3.94s
8:	learn: 53954.3093539	total: 11.7ms	remaining: 3.9s
9:	learn: 52766.3687573	total: 12.9ms	remaining: 3.87s
10:	learn: 51653.0990934	total: 14.1ms	remaining: 3.83s
11:	learn: 50496.1730032	total: 15.3ms	remaining: 3.8s
12:	learn: 49431.7232422	total: 16.4ms	remaining: 3.78s
13:	learn: 48312.7783409	total: 17.6ms	remaining: 3.76s
14:	learn: 47241.4505615	total: 18.7ms	remaining: 3.73s
15:	learn: 46228.1672012	total: 19.9ms	remaining: 3.71s
16:	learn: 45366.0592866	total: 21.1ms	remaining: 3.69s
17:	learn: 44482.8501456	total: 22.3ms	remaining: 3.7s
18:	learn

In [90]:
final

Model   train score   valid score  cross validation
0  catboost  14653.943196  21767.561516          0.889956
1   XGBoost  13076.768079  24689.680306          0.868578
2       rfg  20027.683298  26403.858496          0.840970

### Training

In [130]:
ml_pipeline = Pipeline(
    [
        ('preprocessor', preprocessor),
        ('catboost', CatBoostRegressor(iterations=2500, learning_rate=0.088,depth=6, random_seed=42))
    ]
)
ml_pipeline.fit(X_train,y_train)
root_mean_squared_error(ml_pipeline.predict(X_valid),y_valid)

In [132]:
root_mean_squared_error(ml_pipeline.predict(X_valid),y_valid)

27346.860124904255

### LOG END

In [125]:
ml_pipeline = Pipeline(
    [
        ('preprocessor', preprocessor),
        ('model', CatBoostRegressor(iterations=10000, learning_rate=0.03,depth=7, random_seed=42))
    ]
)


y_log = np.log(y)
ml_pipeline.fit(X, y_log)

0:	learn: 0.3913400	total: 4.02ms	remaining: 40.2s
1:	learn: 0.3834032	total: 7.11ms	remaining: 35.6s
2:	learn: 0.3760484	total: 9.95ms	remaining: 33.2s
3:	learn: 0.3689144	total: 12.8ms	remaining: 31.9s
4:	learn: 0.3618099	total: 15.6ms	remaining: 31.3s
5:	learn: 0.3552012	total: 18.6ms	remaining: 31s
6:	learn: 0.3488752	total: 21.5ms	remaining: 30.6s
7:	learn: 0.3431118	total: 24.7ms	remaining: 30.8s
8:	learn: 0.3370591	total: 27.6ms	remaining: 30.6s
9:	learn: 0.3313274	total: 30.4ms	remaining: 30.4s
10:	learn: 0.3254433	total: 33.2ms	remaining: 30.2s
11:	learn: 0.3200392	total: 36.2ms	remaining: 30.1s
12:	learn: 0.3146034	total: 40.2ms	remaining: 30.9s
13:	learn: 0.3099642	total: 43.1ms	remaining: 30.8s
14:	learn: 0.3049885	total: 46.1ms	remaining: 30.7s
15:	learn: 0.3000357	total: 50.6ms	remaining: 31.5s
16:	learn: 0.2950488	total: 54.2ms	remaining: 31.8s
17:	learn: 0.2901648	total: 57.2ms	remaining: 31.7s
18:	learn: 0.2853705	total: 60.6ms	remaining: 31.8s
19:	learn: 0.2806236	tot

KeyboardInterrupt: 

In [96]:
y_pred = np.exp(ml_pipeline.predict(test))

In [100]:
id = np.arange(1461, 2920)
submission = pd.DataFrame(y_pred).set_index(id).rename(columns={0:'SalePrice'})
submission.to_csv('sub_cbr_2.csv')

In [27]:
ext = train[['LotArea','OverallQual','OverallCond','GrLivArea','GarageCars','SalePrice']]
ext

X, y = ext.drop('SalePrice', axis=1), ext['SalePrice']

In [31]:
class dropper(BaseEstimator, TransformerMixin): 
    
    def fit(self, X, y=None):
        return self
        
    def transform(self, X, y=None):
        X_copy = X.copy()
        return X_copy[['LotArea','OverallQual','OverallCond','GrLivArea','GarageCars']]

dropper_ = ColumnTransformer(
     transformers = [
        ('encode',dropper(),make_column_selector())
     ],
     verbose_feature_names_out = False,
     remainder = 'passthrough')

scaler_ = ColumnTransformer(
     transformers = [
        ('scaler',StandardScaler(),make_column_selector())
     ],
     verbose_feature_names_out = False,
     remainder = 'passthrough')

preprocessor = Pipeline(
    [
        ('dropper',dropper_),
        ('scaler',scaler_)
    ]
)

In [32]:
preprocessor.fit_transform(train)

LotArea  OverallQual  OverallCond  GrLivArea  GarageCars
0    -0.207142     0.651479    -0.517200   0.370333    0.311725
1    -0.091886    -0.071836     2.179628  -0.482512    0.311725
2     0.073480     0.651479    -0.517200   0.515013    0.311725
3    -0.096897     0.651479    -0.517200   0.383659    1.650307
4     0.375148     1.374795    -0.517200   1.299326    1.650307
...        ...          ...          ...        ...         ...
1455 -0.260560    -0.071836    -0.517200   0.250402    0.311725
1456  0.266407    -0.071836     0.381743   1.061367    0.311725
1457 -0.147810     0.651479     3.078570   1.569647   -1.026858
1458 -0.080160    -0.795151     0.381743  -0.832788   -1.026858
1459 -0.058112    -0.795151     0.381743  -0.493934   -1.026858

[1460 rows x 5 columns]

In [33]:
X, y = train.drop('SalePrice', axis=1), train['SalePrice']
path = 'data/test.csv'
test =  pd.read_csv(path)
X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.2, random_state=42)



In [34]:
ml_pipeline = Pipeline(
    [
        ('preprocessor', preprocessor),
        ('catboost', CatBoostRegressor(iterations=2500, learning_rate=0.088,depth=6, random_seed=42))
    ]
)
ml_pipeline.fit(X_train,y_train)
root_mean_squared_error(ml_pipeline.predict(X_valid),y_valid)

0:	learn: 72762.2521846	total: 1.13ms	remaining: 2.82s
1:	learn: 69094.3970282	total: 1.5ms	remaining: 1.87s
2:	learn: 65282.9120507	total: 1.83ms	remaining: 1.52s
3:	learn: 62100.1286866	total: 2.2ms	remaining: 1.37s
4:	learn: 59169.5943285	total: 2.55ms	remaining: 1.27s
5:	learn: 56216.0061084	total: 2.84ms	remaining: 1.18s
6:	learn: 53712.5949421	total: 3.13ms	remaining: 1.11s
7:	learn: 51386.9939366	total: 3.49ms	remaining: 1.09s
8:	learn: 49271.1641570	total: 3.82ms	remaining: 1.06s
9:	learn: 47582.2763465	total: 4.19ms	remaining: 1.04s
10:	learn: 45868.1909658	total: 4.5ms	remaining: 1.02s
11:	learn: 44329.3137402	total: 4.83ms	remaining: 1s
12:	learn: 42985.2967683	total: 5.15ms	remaining: 986ms
13:	learn: 41786.9988217	total: 5.47ms	remaining: 971ms
14:	learn: 40775.4934386	total: 5.79ms	remaining: 960ms
15:	learn: 39890.0559161	total: 6.12ms	remaining: 950ms
16:	learn: 39027.4184637	total: 6.43ms	remaining: 939ms
17:	learn: 38255.4628323	total: 6.76ms	remaining: 932ms
18:	lear

34297.77554009343